# Ejemplo de la vectorización (word2vec, fasttext) del texto de la biblia, se limpia un texto se consigue un archivo vectorizado y se realizan consultas. 

In [1]:
with open('Labiblia-1.txt', 'rb') as source_file:
  with open('labiblia2.txt', 'w+b') as dest_file:
    contents = source_file.read()
    dest_file.write(contents.decode('utf-16').encode('utf-8'))

In [2]:
from gensim.test.utils import common_texts
common_texts[:30]

[['human', 'interface', 'computer'],
 ['survey', 'user', 'computer', 'system', 'response', 'time'],
 ['eps', 'user', 'interface', 'system'],
 ['system', 'human', 'system', 'eps'],
 ['user', 'response', 'time'],
 ['trees'],
 ['graph', 'trees'],
 ['graph', 'minors', 'trees'],
 ['graph', 'minors', 'survey']]

#  Lectura de texto y creación de la lista de sentencias

In [27]:
#!pip3 install -U gensim
import os
import sys
import multiprocessing
import pickle
from gensim.models import FastText

data_set = []

f = open('labiblia2.txt', mode='r', encoding='utf-8').readlines()

for line in f:
    line = line.rstrip("\n")
    data_set.append(line)

In [36]:
from nltk.corpus import stopwords
stop_words = stopwords.words('spanish')
print(stop_words)
se=['cada' ]

['de', 'la', 'que', 'el', 'en', 'y', 'a', 'los', 'del', 'se', 'las', 'por', 'un', 'para', 'con', 'no', 'una', 'su', 'al', 'lo', 'como', 'más', 'pero', 'sus', 'le', 'ya', 'o', 'este', 'sí', 'porque', 'esta', 'entre', 'cuando', 'muy', 'sin', 'sobre', 'también', 'me', 'hasta', 'hay', 'donde', 'quien', 'desde', 'todo', 'nos', 'durante', 'todos', 'uno', 'les', 'ni', 'contra', 'otros', 'ese', 'eso', 'ante', 'ellos', 'e', 'esto', 'mí', 'antes', 'algunos', 'qué', 'unos', 'yo', 'otro', 'otras', 'otra', 'él', 'tanto', 'esa', 'estos', 'mucho', 'quienes', 'nada', 'muchos', 'cual', 'poco', 'ella', 'estar', 'estas', 'algunas', 'algo', 'nosotros', 'mi', 'mis', 'tú', 'te', 'ti', 'tu', 'tus', 'ellas', 'nosotras', 'vosotros', 'vosotras', 'os', 'mío', 'mía', 'míos', 'mías', 'tuyo', 'tuya', 'tuyos', 'tuyas', 'suyo', 'suya', 'suyos', 'suyas', 'nuestro', 'nuestra', 'nuestros', 'nuestras', 'vuestro', 'vuestra', 'vuestros', 'vuestras', 'esos', 'esas', 'estoy', 'estás', 'está', 'estamos', 'estáis', 'están', 'e

# El paquete de stopwords-siso de python está definido para 57 lenguajes 

In [2]:
!pip3 install stopwordsiso

Please see https://github.com/pypa/pip/issues/5599 for advice on fixing the underlying issue.
To avoid this problem you can invoke Python with '-m pip' instead of running pip directly.
     |████████████████████████████████| 73 kB 5.7 MB/s eta 0:00:011


In [4]:
import stopwordsiso as stopwords
stopwords.stopwords('es')

{'0',
 '1',
 '2',
 '3',
 '4',
 '5',
 '6',
 '7',
 '8',
 '9',
 '_',
 'a',
 'actualmente',
 'acuerdo',
 'adelante',
 'ademas',
 'además',
 'adrede',
 'afirmó',
 'agregó',
 'ahi',
 'ahora',
 'ahí',
 'al',
 'algo',
 'alguna',
 'algunas',
 'alguno',
 'algunos',
 'algún',
 'alli',
 'allí',
 'alrededor',
 'ambos',
 'ampleamos',
 'antano',
 'antaño',
 'ante',
 'anterior',
 'antes',
 'apenas',
 'aproximadamente',
 'aquel',
 'aquella',
 'aquellas',
 'aquello',
 'aquellos',
 'aqui',
 'aquél',
 'aquélla',
 'aquéllas',
 'aquéllos',
 'aquí',
 'arriba',
 'arribaabajo',
 'aseguró',
 'asi',
 'así',
 'atras',
 'aun',
 'aunque',
 'ayer',
 'añadió',
 'aún',
 'b',
 'bajo',
 'bastante',
 'bien',
 'breve',
 'buen',
 'buena',
 'buenas',
 'bueno',
 'buenos',
 'c',
 'cada',
 'casi',
 'cerca',
 'cierta',
 'ciertas',
 'cierto',
 'ciertos',
 'cinco',
 'claro',
 'comentó',
 'como',
 'con',
 'conmigo',
 'conocer',
 'conseguimos',
 'conseguir',
 'considera',
 'consideró',
 'consigo',
 'consigue',
 'consiguen',
 'consi

# Tokenización de las sentencias

In [37]:
from nltk.corpus import stopwords
sentences = []
diccionario = dict()

for i, sent in enumerate(data_set):
    if i >= 0:
        if len(sent) > 1:
            sente = sent.split()
            sentences.append(sente)
           # tokens = word_tokenize(sentences)
            
print(sentences[1:10])
print('No. Oraciones en train dataset: ', len(sentences))


[['VERSIÓN', 'BIBLIA', 'DE', 'JERUSALÉN,', '1976'], ['GÉNESIS'], ['Génesis', '1'], ['1', 'En', 'el', 'principio', 'creó', 'Dios', 'los', 'cielos', 'y', 'la', 'tierra.'], ['2', 'La', 'tierra', 'era', 'caos', 'y', 'confusión', 'y', 'oscuridad', 'por', 'encima', 'del', 'abismo,', 'y', 'un', 'viento', 'de', 'Dios', 'aleteaba', 'por', 'encima', 'de', 'las', 'aguas.'], ['3', 'Dijo', 'Dios:', '«Haya', 'luz»,', 'y', 'hubo', 'luz.'], ['4', 'Vio', 'Dios', 'que', 'la', 'luz', 'estaba', 'bien,', 'y', 'apartó', 'Dios', 'la', 'luz', 'de', 'la', 'oscuridad;'], ['5', 'y', 'llamó', 'Dios', 'a', 'la', 'luz', '«día»,', 'y', 'a', 'la', 'oscuridad', 'la', 'llamó', '«noche».', 'Y', 'atardeció', 'y', 'amaneció:', 'día', 'primero.'], ['6', 'Dijo', 'Dios:', '«Haya', 'un', 'firmamento', 'por', 'en', 'medio', 'de', 'las', 'aguas,', 'que', 'las', 'aparte', 'unas', 'de', 'otras.»']]
No. Oraciones en train dataset:  36945


# Preprocesamiento de las sentencias y limpieza del texto

1. Eliminación de los números del texto
2. Eliminación de las palabras stopwords 
3. Eliminación de la puntuación
4. Eliminació de otros símbolos especiales


In [38]:
import re, string
sentences.pop(0)
sentencias1=[]
for nom in sentences:
    newstring = [i for i in nom if not i.isdigit()]
    stop_words = stopwords.words('spanish')
    newstring = [w for w in newstring if not w in stop_words]
    re_punc = re.compile('[%s]' % re.escape(string.punctuation))
    newstring = [re_punc.sub('', w) for w in newstring]
    newstring = [re.sub("\!|\'|\?|\¿|\¡|\«","",w) for w in newstring]
    sentencias1.append(newstring)
    print(newstring)
    print(len(newstring))

['VERSIÓN', 'BIBLIA', 'DE', 'JERUSALÉN']
4
['GÉNESIS']
1
['Génesis']
1
['En', 'principio', 'creó', 'Dios', 'cielos', 'tierra']
6
['La', 'tierra', 'caos', 'confusión', 'oscuridad', 'encima', 'abismo', 'viento', 'Dios', 'aleteaba', 'encima', 'aguas']
12
['Dijo', 'Dios', 'Haya', 'luz»', 'luz']
5
['Vio', 'Dios', 'luz', 'bien', 'apartó', 'Dios', 'luz', 'oscuridad']
8
['llamó', 'Dios', 'luz', 'día»', 'oscuridad', 'llamó', 'noche»', 'Y', 'atardeció', 'amaneció', 'día', 'primero']
12
['Dijo', 'Dios', 'Haya', 'firmamento', 'medio', 'aguas', 'aparte', 'unas', 'otras»']
9
['E', 'hizo', 'Dios', 'firmamento', 'apartó', 'aguas', 'debajo', 'firmamento', 'aguas', 'encima', 'firmamento', 'Y', 'así', 'fue']
14
['Y', 'llamó', 'Dios', 'firmamento', 'cielos»', 'Y', 'atardeció', 'amaneció', 'día', 'segundo']
10
['Dijo', 'Dios', 'Acumúlense', 'aguas', 'debajo', 'firmamento', 'solo', 'conjunto', 'déjese', 'ver', 'seco»', 'así', 'fue']
13
['Y', 'llamó', 'Dios', 'seco', 'tierra»', 'conjunto', 'aguas', 'llamó', 

In [39]:
print('No. Oraciones en train dataset: ', len(sentencias1))

print(data_set[:3])

No. Oraciones en train dataset:  36944
['LA SANTA BIBLIA', '', '']


In [40]:
print(sentencias1[1:3])
print(sentencias1[100])

[['GÉNESIS'], ['Génesis']]
['Respondióle', 'Yahvéh', 'Al', 'contrario', 'quienquiera', 'matare', 'Caín', 'pagará', 'siete', 'veces»', 'Y', 'Yahvéh', 'puso', 'señal', 'Caín', 'nadie', 'encontrase', 'atacara']


In [41]:
print ("numero de oraciones presentes en el corpus: " + str(len(sentencias1)))
print ("                 numero de palabras unicas: " + str(len(diccionario)))

numero de oraciones presentes en el corpus: 36944
                 numero de palabras unicas: 0


# Características de la construcción del vector

In [34]:
num_features = [300]                      #Dimensionality of the resulting word vectors
min_word_count = 1                        #Minimum word count threshold
num_workers = multiprocessing.cpu_count() #Number of threads to run in parallel
context_size = 5                          #Context window length
seed = 1  


In [35]:
for p in num_features:
    fasttext_model = FastText(
        sentences=sentencias1,
        size=300,
        window=context_size,
        min_count=min_word_count,
        workers=num_workers, 
        sg=0                              #cbow
    )

    fasttext_model.wv.save_word2vec_format('./biblia_fasttext_cbow_model_' + str(p) +  '.txt', binary=False)
    
    #del fasttext_model

In [50]:
model.wv.most_similar('Dios')

[('Excelso', 0.9919581413269043),
 ('Alabad', 0.9916894435882568),
 ('emplazará', 0.9915157556533813),
 ('“Nosotros', 0.9913273453712463),
 ('truena', 0.9911696910858154),
 ('Líbreme', 0.9909036159515381),
 ('Yahvéh', 0.9901056289672852),
 ('creador', 0.9896005392074585),
 ('glorificando', 0.9894495010375977),
 ('Bendecid', 0.9893947243690491)]

# Consultas con Word2vec sobre la Biblia

In [42]:
from gensim.models import Word2Vec                                      #Seed for the RNG, to make the result reproducible
model = Word2Vec(sentences=sentencias1,size=300, window=5, min_count=1, workers=4)
model.save("word2vec.model")

In [43]:
model['fe']


/home/deep/.local/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  """Entry point for launching an IPython kernel.


array([-0.41447693, -0.60505694, -0.24979562, -0.2236599 ,  0.04409919,
       -0.30525443,  0.19274862, -0.09537642, -0.3171298 , -0.13892496,
        0.0171346 , -0.1905566 , -0.08126915, -0.08226623,  0.1667672 ,
        0.18892726,  0.03554835,  0.23084383,  0.28438833,  0.15259618,
       -0.26743144, -0.28854132, -0.29870027, -0.52582353, -0.08585867,
        0.45558655, -0.29523313,  0.5695251 , -0.00639893, -0.10886475,
        0.01407181,  0.22913997, -0.661904  , -0.77708495,  0.16795184,
       -0.3321814 , -0.08356918,  0.08806355,  0.2822243 ,  0.39478335,
       -0.01443473,  0.5250807 ,  0.43872553,  0.98716474,  0.00156515,
        0.32118064,  0.47238967,  0.39345324,  0.09007248, -0.30747953,
       -0.65396345,  0.14032018,  0.2851481 , -0.30668032,  0.18272817,
       -0.5660752 , -0.26264232,  0.31779015, -0.3136994 , -0.34941933,
        0.2924874 ,  0.13352083,  0.1962373 ,  0.7012582 ,  0.02295471,
        0.14300245, -0.26573285,  0.3895526 , -0.5901566 , -0.08

In [44]:
model = Word2Vec.load("word2vec.model")
sims1 = model.wv.most_similar("Jesús", topn=10)  # get other similar words
print(sims1)

[('Qué', 0.9984471797943115), ('Job', 0.9980010986328125), ('Ángel', 0.9977892637252808), ('Hijo', 0.9972742795944214), ('paz»', 0.9972628951072693), ('soy»', 0.9969369173049927), ('términos', 0.9968881607055664), ('conociendo', 0.9968768954277039), ('ángel', 0.9968335628509521), ('Verdaderamente', 0.9967976212501526)]


In [32]:
resultados1 = model.wv.most_similar(positive=['Abraham', 'Sara'], negative=['Isaac'])
#most_similar = similarities[0]
print(resultados1)

[('Natán', 0.997840166091919), ('padre»', 0.9973510503768921), ('reinará', 0.9967675805091858), ('Oseas', 0.9963423013687134), ('Balaq', 0.9959169626235962), ('Vete', 0.9958608746528625), ('mío»', 0.9954782724380493), ('llamó', 0.9952872395515442), ('Gedeón', 0.9952528476715088), ('Tobías', 0.9951374530792236)]


In [33]:
from gensim.models import FastText
model1 = FastText(sentences=sentencias1, window=5, min_count=1, workers=4)

In [34]:
sims1 = model1.wv.most_similar('Jesús', topn=10)  # get other similar words
print(sims1)

[('Jesús»', 0.9990713596343994), ('Le', 0.9974085092544556), ('Affús', 0.9965417385101318), ('Rey', 0.9964553713798523), ('Clamé', 0.9963828325271606), ('Profeta', 0.9962250590324402), ('Es', 0.996109664440155), ('Jefsí', 0.9960547685623169), ('Id»', 0.9958294034004211), ('Ve', 0.9953967332839966)]


In [47]:
with open('word2vec_skip-gram_model_300.txt', 'rb') as source_file:
  with open('word2vec_skip-gram_model_300-utf8.txt', 'w+b') as dest_file:
    contents = source_file.read()
    dest_file.write(contents.decode('utf-16').encode('utf-8'))

In [49]:
# load Google News pre-trained network
from gensim.models import KeyedVectors
model = KeyedVectors.load_word2vec_format("biblia_fasttext_cbow_model_300.txt", binary=True)

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xa9 in position 0: invalid start byte